### Snowballing

objective: this part of code aims at exapanding the synonyms network

input: wordlist of 1st synonym extraction

output: node, edge list after expandsion 


In [1]:
import requests
import json
from collections import defaultdict
import pandas as pd 
import numpy as np
import json 
import os
from datetime import datetime
from collections import Counter
import re

In [5]:
second1k = pd.read_csv("word_list.csv")

In [6]:
full_expand2 = set()

for item_list in second1k['synlist']:
    for item in re.findall('([\w-]+)',item_list):
        full_expand2.add(item)
seed_word = set(second1k['word'].unique())

In [7]:
second1k['synlist_formatted']=second1k['synlist'].apply(lambda x: re.findall('([\w-]+)',x))
second1k['syn_len']=second1k['synlist_formatted'].str.len()

In [8]:
second1k.head()

word               pos_sub  \
0  factual  factual_adjective_01   
1  factual  factual_adjective_02   
2    sting         sting_verb_01   
3    sting         sting_verb_02   
4    sting         sting_noun_01   

                                             synlist  \
0  ['documentary', 'hard', 'historical', 'literal...   
1  ['actual', 'concrete', 'effective', 'existent'...   
2       ['gouge', 'overcharge', 'soak', 'surcharge']   
3  ['beat', 'bilk', 'bleed', 'cheat', 'chisel', '...   
4  ['bunco', 'con', 'fiddle', 'flimflam', 'fraud'...   

                                   synlist_formatted  syn_len  
0  [documentary, hard, historical, literal, matte...        8  
1  [actual, concrete, effective, existent, genuin...        9  
2               [gouge, overcharge, soak, surcharge]        4  
3  [beat, bilk, bleed, cheat, chisel, chouse, con...       35  
4  [bunco, con, fiddle, flimflam, fraud, hustle, ...        8

In [9]:
print(f'number of seed words : {len(seed_word)}')
print(f'number of expanded words (exclude seedwords) : {len(full_expand2 - seed_word)}')
print(f'expansion rate {len(full_expand2 - seed_word)/len(seed_word)}')

number of seed words : 827
number of expanded words (exclude seedwords) : 13796
expansion rate 16.681983071342202


In [100]:
second1k.sum()

word                 factualfactualstingstingstingstingmidmidmillen...
pos_sub              factual_adjective_01factual_adjective_02sting_...
synlist              ['documentary', 'hard', 'historical', 'literal...
synlist_formatted    [documentary, hard, historical, literal, matte...
syn_len                                                          30311
dtype: object

In [33]:
new_final=pd.DataFrame(columns=['source','dest'])
for root in second1k['word']:
    dest = []
    for word in second1k.loc[second1k['word']==str(root),'synlist_formatted'].tolist():
        dest.extend(word)
        source = [root for i in range(len(dest))]
        new = pd.DataFrame({'source':source,'dest':dest})
        new_final=pd.concat([new_final,new])
new_final=new_final.drop_duplicates()
# not in source
dest_filter1=[]
for word in new_final['dest'].tolist():
    if word not in new_final['source'].tolist():
        dest_filter1.append(word)
dest_filtered=pd.DataFrame({'new_dest':dest_filter1})
dest_filtered

In [101]:
# only appear once in the dest
dest_filter2 = dest_filtered[dest_filtered.groupby('new_dest').new_dest.transform(len) > 1]
#node list
dest_filter2.columns=['Node']
dest_filter2

In [104]:
snow_ball=set(new_final['source'].tolist()+new_final['dest'].tolist())

In [105]:
len(snow_ball)

5691

In [108]:
pd.DataFrame(snow_ball).to_csv('snow_ball.csv')

In [109]:
dest_filter2.to_csv('node_list.csv')

In [111]:
new_final.to_csv('edge_list', index=False)

In [112]:
snow_ball


{'twitter',
 'emperor',
 'intellect',
 'dispose',
 'garb',
 'antsy',
 'interfused',
 'track',
 'out-of-sight',
 'discombobulate',
 'grievous',
 'invented',
 'travel',
 'force',
 'accept',
 'weakened',
 'muss',
 'scandalous',
 'radical',
 'heaven',
 'blazing',
 'swarm',
 'spit',
 'czar',
 'dab',
 'embellishment',
 'unintended',
 'kid',
 'shifting',
 'audacious',
 'extravagant',
 'betide',
 'small',
 'disquiet',
 'oceanic',
 'relent',
 'shower',
 'out-and-out',
 'forecast',
 'kindness',
 'instigate',
 'under',
 'calculate',
 'caricature',
 'unlovely',
 'success',
 'plunder',
 'squeaky-clean',
 'collapse',
 'beasts',
 'cease',
 'royal',
 'scathe',
 'oppression',
 'mimic',
 'downy',
 'genus',
 'solo',
 'eye-catching',
 'thump',
 'gratified',
 'exercise',
 'truly',
 'enrobe',
 'trunk',
 'cessation',
 'frost',
 'hack',
 'foretell',
 'info',
 'po-faced',
 'mere',
 'betray',
 'rubric',
 'worrying',
 'inclement',
 'quietness',
 'floor',
 'mew',
 'superintend',
 'toil',
 'hare',
 'concise',
 'en

In [125]:
df2=pd.DataFrame(new_final['source']).drop_duplicates()

In [126]:
df2.columns=['Node']

In [131]:
final_node=pd.concat([df2,dest_filter2],ignore_index=True)

In [133]:
final_node.to_csv('final_node_list.csv')

###  Use previous extraction code to get 2nd interation of synonyms

### Update node & edge list

In [2]:
seconditer = pd.read_csv('word_list.csv')

In [3]:
seconditer['synlist_formatted']=seconditer['synlist'].apply(lambda x: re.findall('([\w-]+)',x))
seconditer['syn_len']=seconditer['synlist_formatted'].str.len()

In [4]:
seconditer

word                 pos_sub  \
0      aberrated  aberrated_adjective_01   
1          class           class_noun_01   
2          class           class_noun_02   
3          class           class_noun_03   
4          class           class_noun_04   
...          ...                     ...   
17315       cool            cool_verb_01   
17316       cool            cool_verb_02   
17317       cool            cool_noun_01   
17318       cool            cool_noun_02   
17319       cool            cool_noun_03   

                                                 synlist  \
0      ['aberrant', 'abnormal', 'anomalous', 'atypica...   
1      ['caste', 'estate', 'folk', 'gentry', 'order',...   
2      ['bracket', 'category', 'classification', 'div...   
3      ['breed', 'description', 'feather', 'genre', '...   
4                                             ['course']   
...                                                  ...   
17315                           ['chill', 'refrigerate']   
17316                     ['chill out', 'hush', 'quiet']   
17317  ['coldness', 'detachment', 'dispassion', 'disp...   
17318  ['coolness', 'fashionableness', 'hip', 'hipnes...   
17319  ['aplomb', 'calmness', 'collectedness', 'compo...   

                                       synlist_formatted  syn_len  
0      [aberrant, abnormal, anomalous, atypical, espe...       21  
1          [caste, estate, folk, gentry, order, stratum]        6  
2      [bracket, category, classification, division, ...       18  
3      [breed, description, feather, genre, ilk, kidn...       17  
4                                               [course]        1  
...                                                  ...      ...  
17315                               [chill, refrigerate]        2  
17316                          [chill, out, hush, quiet]        4  
17317  [coldness, detachment, dispassion, dispassiona...        4  
17318  [coolness, fashionableness, hip, hipness, hips...        9  
17319  [aplomb, calmness, collectedness, composedness...       18  

[17320 rows x 5 columns]

In [146]:
node_edge=pd.DataFrame(columns=['source','dest'])
dests = []
sources =[]
for root in seconditer['word'].unique():
    dest=[]
    for word in seconditer.loc[seconditer['word']==str(root),'synlist_formatted'].tolist():
        dest.extend(word)
#     print(dest)
    source = [root for i in range(len(dest))]
#     print(source)
    dests.extend(dest)
    sources.extend(source)      

['aberrant', 'abnormal', 'anomalous', 'atypical', 'especial', 'exceeding', 'exceptional', 'extraordinaire', 'extraordinary', 'freak', 'odd', 'peculiar', 'phenomenal', 'preternatural', 'rare', 'singular', 'uncommon', 'uncustomary', 'unique', 'unusual', 'unwonted']
['aberrated', 'aberrated', 'aberrated', 'aberrated', 'aberrated', 'aberrated', 'aberrated', 'aberrated', 'aberrated', 'aberrated', 'aberrated', 'aberrated', 'aberrated', 'aberrated', 'aberrated', 'aberrated', 'aberrated', 'aberrated', 'aberrated', 'aberrated', 'aberrated']
['caste', 'estate', 'folk', 'gentry', 'order', 'stratum', 'bracket', 'category', 'classification', 'division', 'family', 'genus', 'grade', 'group', 'kind', 'league', 'order', 'rank', 's', 'rubric', 'set', 'species', 'tier', 'type', 'breed', 'description', 'feather', 'genre', 'ilk', 'kidney', 'kind', 'like', 'manner', 'nature', 'order', 'sort', 'species', 'strain', 'stripe', 'type', 'variety', 'course', 'caliber', 'grade', 'quality', 'rate', 'classiness', 'co

['soul', 'spirit', 'brain', 'cerebrum', 'head', 'mind', 'thinker']
['psyche', 'psyche', 'psyche', 'psyche', 'psyche', 'psyche', 'psyche']
['bizarre', 'bizarro', 'cranky', 'crazy', 'curious', 'eccentric', 'erratic', 'far-out', 'funky', 'funny', 'kinky', 'kooky', 'odd', 'off-kilter', 'off-the-wall', 'offbeat', 'out-of-the-way', 'outlandish', 'outré', 'peculiar', 'quaint', 'queer', 'queerish', 'quirky', 'remarkable', 'screwy', 'spaced-out', 'strange', 'wacky', 'way-out', 'weird', 'weirdo', 'wild', 'alcohol', 'ardent', 'spirits', 'booze', 'bottle', 'drink', 'firewater', 'grog', 'hooch', 'inebriant', 'intoxicant', 'juice', 'liquor', 'lush', 'moonshine', 'potable', 'sauce', 'spirits', 'stimulant', 'tipple']
['rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', 'rum', '

['depose', 'deposit', 'dispose', 'emplace', 'fix', 'lay', 'place', 'position', 'put', 'set', 'stick']
['situate', 'situate', 'situate', 'situate', 'situate', 'situate', 'situate', 'situate', 'situate', 'situate', 'situate']
['biggish', 'considerable', 'good', 'goodly', 'handsome', 'healthy', 'largish', 'respectable', 'significant', 'sizable', 'substantial', 'substantive', 'tidy', 'big', 'consequential', 'earth-shattering', 'earthshaking', 'eventful', 'historic', 'important', 'material', 'meaningful', 'momentous', 'monumental', 'much', 'significant', 'substantial', 'tectonic', 'weighty']
['major', 'major', 'major', 'major', 'major', 'major', 'major', 'major', 'major', 'major', 'major', 'major', 'major', 'major', 'major', 'major', 'major', 'major', 'major', 'major', 'major', 'major', 'major', 'major', 'major', 'major', 'major', 'major', 'major']
['cool', 'coolness', 'fashionableness', 'hip', 'hipness', 'hipsterism', 'modishness', 'stylishness', 'trendiness', 'fashionability', 'fashionabl

['cagey', 'disinclined', 'dubious', 'hesitant', 'loath', 'reluctant', 'reticent', 'ailing', 'bad', 'down', 'ill', 'peaked', 'peaky', 'poorly', 'punk', 'run-down', 'sick', 'sickened', 'unhealthy', 'unsound', 'unwell']
['indisposed', 'indisposed', 'indisposed', 'indisposed', 'indisposed', 'indisposed', 'indisposed', 'indisposed', 'indisposed', 'indisposed', 'indisposed', 'indisposed', 'indisposed', 'indisposed', 'indisposed', 'indisposed', 'indisposed', 'indisposed', 'indisposed', 'indisposed', 'indisposed']
['impenetrability', 'inscrutability', 'mysteriousness', 'numinousness', 'obscurity', 'uncanniness', 'ambiguity', 'ambiguousness', 'darkness', 'equivocalness', 'equivocation', 'inscrutability', 'murkiness', 'mysteriousness', 'nebulosity', 'nebulousness', 'obliqueness', 'obliquity', 'obscurity', 'opacity', 'opaqueness']
['inscrutableness', 'inscrutableness', 'inscrutableness', 'inscrutableness', 'inscrutableness', 'inscrutableness', 'inscrutableness', 'inscrutableness', 'inscrutablenes

['echo', 'resonate', 'resound', 'reverberate', 'sound', 'ditto', 'echo', 'parrot', 'quote', 'repeat']
['reecho', 'reecho', 'reecho', 'reecho', 'reecho', 'reecho', 'reecho', 'reecho', 'reecho', 'reecho']
['cloistered', 'covert', 'isolated', 'quiet', 'remote', 'retired', 'secluded', 'secret', 'sheltered', 'buried', 'cached', 'concealed', 'ensconced', 'secreted', 'belied', 'blanketed', 'cloaked', 'concealed', 'covered', 'curtained', 'disguised', 'enshrouded', 'masked', 'obscured', 'occulted', 'screened', 'shrouded', 'suppressed', 'veiled', 'lain', 'lurked', 'reposed', 'skulked']
['hidden', 'hidden', 'hidden', 'hidden', 'hidden', 'hidden', 'hidden', 'hidden', 'hidden', 'hidden', 'hidden', 'hidden', 'hidden', 'hidden', 'hidden', 'hidden', 'hidden', 'hidden', 'hidden', 'hidden', 'hidden', 'hidden', 'hidden', 'hidden', 'hidden', 'hidden', 'hidden', 'hidden', 'hidden', 'hidden', 'hidden', 'hidden', 'hidden']
['aching', 'agonized', 'anguished', 'bemoaning', 'bewailing', 'bitter', 'deploring', '

...

['coarse', 'common', 'crude', 'gross', 'ill-bred', 'illiberal', 'incult', 'insensible', 'low', 'lowbred', 'lowbrow', 'raffish', 'rough', 'rough-hewn', 'roughneck', 'rude', 'rugged', 'tasteless', 'uncouth', 'uncultivated', 'uncultured', 'unpolished', 'unrefined', 'vulgar']
['crass', 'crass', 'crass', 'crass', 'crass', 'crass', 'crass', 'crass', 'crass', 'crass', 'crass', 'crass', 'crass', 'crass', 'crass', 'crass', 'crass', 'crass', 'crass', 'crass', 'crass', 'crass', 'crass', 'crass']
['authoritative', 'forceful', 'weighty', 'heavy', 'heavy-duty', 'important', 'mighty', 'potent', 'powerful', 'puissant', 'significant', 'strong']
['influential', 'influential', 'influential', 'influential', 'influential', 'influential', 'influential', 'influential', 'influential', 'influential', 'influential', 'influential']
['befoul', 'begrime', 'bemire', 'besmirch', 'blacken', 'dirty', 'distain', 'foul', 'gaum', 'grime', 'mire', 'muck', 'muddy', 'smirch', 'smudge', 'soil', 'stain', 'sully', 'anoint', 'b

['administer', 'administrate', 'conduct', 'control', 'direct', 'govern', 'guide', 'handle', 'keep', 'manage', 'operate', 'overlook', 'regulate', 'run', 'steward', 'superintend', 'supervise', 'tend', 'boss', 'captain', 'handle', 'head', 'overlook', 'quarterback', 'superintend', 'supervise', 'attend', 'mind', 'superintend', 'supervise', 'tend', 'watch', 'audit', 'con', 'examine', 'inspect', 'overlook', 'review', 'scan', 'scrutinize', 'survey', 'view']
['oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee', 'oversee']
['author', 'begetter', 'creator', 'establisher', 'father', 'founder', 'generator', 

['additionally', 'again', 'also', 'besides', 'either', 'further', 'furthermore', 'likewise', 'more', 'then', 'too', 'withal', 'yet']
['moreover', 'moreover', 'moreover', 'moreover', 'moreover', 'moreover', 'moreover', 'moreover', 'moreover', 'moreover', 'moreover', 'moreover', 'moreover']
['compensation', 'damages', 'indemnification', 'indemnity', 'quittance', 'recoupment', 'redress', 'remuneration', 'reparation', 'reprisal', 's', 'requital', 'restitution', 'satisfaction', 'compensation', 'consideration', 'pay', 'payment', 'remittance', 'remuneration', 'requital', 'compensate', 'pay', 'remunerate', 'balance', 'clear', 'discharge', 'foot', 'liquidate', 'meet', 'pay', 'pay', 'up', 'quit', 'settle', 'stand', 'compensate', 'indemnify', 'recoup', 'remunerate', 'requite', 'satisfy', 'reciprocate', 'repay', 'requite']
['recompense', 'recompense', 'recompense', 'recompense', 'recompense', 'recompense', 'recompense', 'recompense', 'recompense', 'recompense', 'recompense', 'recompense', 'recompe

['aft', 'after', 'back', 'hind', 'hinder', 'hindmost', 'posterior', 'rearward', 'back', 'reverse', 'tail', 'backside', 'behind', 'booty', 'bottom', 'breech', 'bum', 'buns', 'butt', 'buttocks', 'caboose', 'can', 'cheeks', 'derriere', 'duff', 'fanny', 'fundament', 'hams', 'haunches', 'heinie', 'hunkers', 'keister', 'nates', 'posterior', 'rump', 'seat', 'tail', 'tush', 'breed', 'foster', 'nourish', 'nurse', 'raise', 'erect', 'pitch', 'raise', 'upend', 'upraise', 'assemble', 'build', 'confect', 'construct', 'erect', 'fabricate', 'make', 'piece', 'raise', 'crop', 'cultivate', 'culture', 'dress', 'grow', 'promote', 'raise', 'tend']
['rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear', 'rear

['chaste', 'clean', 'decent', 'G-rated', 'modest', 'pure', 'vestal', 'virgin', 'virginal', 'antiseptic', 'chaste', 'clean', 'fair', 'pristine', 'spick-and-span', 'spotless', 'squeaky-clean', 'stainless', 'unsoiled', 'unstained', 'unsullied', 'absolute', 'faultless', 'flawless', 'ideal', 'impeccable', 'indefectible', 'irreproachable', 'letter-perfect', 'perfect', 'picture-book', 'picture-perfect', 'seamless', 'unblemished']
['immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate', 'immaculate']
['bloc', 'block', 'body', 'faction', 'party', 'sect', 'set', 'side', 'wing', 'alliance', 'axis',

In [100]:
node_edge = pd.DataFrame({'source':sources,'target':dests})

In [102]:
print(f"second iteration seed word counts:{len(seconditer['word'].unique())}")
print(f"second iteration seed word counts:{len(node_edge['target'].unique())}")
print(f'expansion rate (unique words): {26196/5654}')

second iteration seed word counts:5654
second iteration seed word counts:26196
expansion rate (unique words): 4.633180049522462


In [104]:
flatten = node_edge['source'].tolist()
flatten.extend(node_edge['target'].tolist())

In [105]:
c = Counter(flatten)

In [106]:
for degree in range(1,6):
    count_of_nodes = len(dict(filter(lambda elem: elem[1]>=degree,dict(c).items())).keys())
    print(f'count of degree >={degree} : {count_of_nodes} ')

count of degree >=1 : 26215 
count of degree >=2 : 19033 
count of degree >=3 : 15344 
count of degree >=4 : 13244 
count of degree >=5 : 11560 


In [47]:
len(node_edge)

248966

In [108]:
for degree in range(0,6):
    degree2 =dict(filter(lambda elem: elem[1]>degree,dict(c).items())).keys()
    print(f"count of edges with =degree {degree}: {len(node_edge.loc[node_edge['source'].isin(degree2)&node_edge['target'].isin(degree2)])}")

count of edges with =degree 0: 248966
count of edges with =degree 1: 241785
count of edges with =degree 2: 234411
count of edges with =degree 3: 228116
count of edges with =degree 4: 221390
count of edges with =degree 5: 215423


In [145]:
dict(filter(lambda elem: elem[1]>4,dict(c).items())).keys()
edge_list = node_edge.loc[node_edge['source'].isin(degree2)&node_edge['target'].isin(degree2)]

In [110]:
edge_list['weight']=1

/Users/nanyang/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [113]:
nodes = edge_list['source'].unique().tolist()
nodes.extend(edge_list['target'].unique().tolist())
nodes = list(set(nodes))
nodes_df=pd.DataFrame({'label':nodes})
nodes_df['id']=nodes_df.index
nodes_df.to_csv('second_iteration_nodes_updated.csv',index=False)
### dic of label and id 
node_list ={}
for key in nodes_df['label'].tolist():
    node_list[key]=nodes_df.loc[nodes_df['label']==key,'id'].values[0]
edge_list['source']=edge_list['source'].map(node_list)
edge_list['target']=edge_list['target'].map(node_list)
edge_list['weight']=1
edge_list.to_csv('second_iteration_edge_list_updated.csv',index=False)